In [1]:
import pandas as pd
import numpy as np
from scipy.sparse import csr_matrix, csc_matrix

# Loading the data and preprocessing it

In [2]:
movies = pd.read_csv('ml-1m/ml-1m/movies.dat', sep='::', header=None, engine='python', encoding='ISO-8859-1', names=['MovieID', 'Title', 'Genres'])
ratings = pd.read_csv('ml-1m/ml-1m/ratings.dat', sep='::', header=None, engine='python', encoding='ISO-8859-1', names=['UserID', 'MovieID', 'Rating', 'Timestamp'])
users = pd.read_csv('ml-1m/ml-1m/users.dat', sep='::', header=None, engine='python', encoding='ISO-8859-1', names=['UserID', 'Gender', 'Age', 'Occupation', 'Zip-code'])

# Rebase IDs to be contiguous integers 0...N-1 (useful for matrix indexing)
user2idx = {old: new for new, old in enumerate(users['UserID'].unique())}
movie2idx = {old: new for new, old in enumerate(movies['MovieID'].unique())}

users['UserID'] = users['UserID'].map(user2idx)
movies['MovieID'] = movies['MovieID'].map(movie2idx)
ratings['UserID'] = ratings['UserID'].map(user2idx)
ratings['MovieID'] = ratings['MovieID'].map(movie2idx)

print('Movies shape:', movies.shape)
print(movies.head())
print('\n')

movies['Genres'] = movies['Genres'].str.split('|').apply(lambda x: set(x))
genres_set = set().union(*movies['Genres'])

print('Ratings shape:', ratings.shape)
print(ratings.head())
print('\n')

print('Users shape:', users.shape)
print(users.head())
print('\n')

print('Genres:', genres_set)

Movies shape: (3883, 3)
   MovieID                               Title                        Genres
0        0                    Toy Story (1995)   Animation|Children's|Comedy
1        1                      Jumanji (1995)  Adventure|Children's|Fantasy
2        2             Grumpier Old Men (1995)                Comedy|Romance
3        3            Waiting to Exhale (1995)                  Comedy|Drama
4        4  Father of the Bride Part II (1995)                        Comedy


Ratings shape: (1000209, 4)
   UserID  MovieID  Rating  Timestamp
0       0     1176       5  978300760
1       0      655       3  978302109
2       0      902       3  978301968
3       0     3339       4  978300275
4       0     2286       5  978824291


Users shape: (6040, 5)
   UserID Gender  Age  Occupation Zip-code
0       0      F    1          10    48067
1       1      M   56          16    70072
2       2      M   25          15    55117
3       3      M   45           7    02460
4       4      M

We turn rating into binary variables

In [3]:
ratings['binary_rating'] = ratings['Rating'].apply(lambda x: 1 if x >= 4 else 0)
ratings["Timestamp"] = pd.to_datetime(ratings["Timestamp"], unit='s')
ratings.head()

UserID  MovieID  Rating           Timestamp  binary_rating
0       0     1176       5 2000-12-31 22:12:40              1
1       0      655       3 2000-12-31 22:35:09              0
2       0      902       3 2000-12-31 22:32:48              0
3       0     3339       4 2000-12-31 22:04:35              1
4       0     2286       5 2001-01-06 23:38:11              1

In [4]:
# Create a set of triplets (UserID, MovieID, binary_rating)
ratings_triplets = set(zip(ratings['UserID'], ratings['MovieID'], ratings['binary_rating']))

# Verify the result
print(f'Number of unique triplets: {len(ratings_triplets)}')
list(ratings_triplets)[:5]

Number of unique triplets: 1000209


[(5792, 2878, 1),
 (5112, 1884, 0),
 (5305, 1899, 0),
 (3642, 1575, 1),
 (4219, 896, 1)]

# Creating the KNN bandit class

In [5]:
class KNNBandit:
    def __init__(self, k, ratings, alpha_prior=1.0, beta_prior=1.0):
        """
        Initializes the Nearest-Neighbor Bandit with optimized sparse structures.
        
        Args:
            k (int): Number of neighbors to consult.
            ratings (pd.DataFrame): Dataframe with columns ['UserID', 'MovieID', 'binary_rating'].
            alpha_prior (float): Initial value for alpha (successes). Must be > 0.
            beta_prior (float): Initial value for beta (failures). Must be > 0.
        """
        self.k = k
        self.alpha_prior = alpha_prior
        self.beta_prior = beta_prior
        
        # --- 1. ID MAPPING ---
        # Convert distinct IDs to continuous indices (0 to N-1) for matrix operations
        self.user_ids = ratings['UserID'].unique()
        self.item_ids = ratings['MovieID'].unique()
        
        self.user_map = {uid: i for i, uid in enumerate(self.user_ids)}
        self.item_map = {iid: i for i, iid in enumerate(self.item_ids)}
        
        # Reverse map to return real IDs later
        self.rev_user_map = {i: uid for uid, i in self.user_map.items()}
        self.rev_item_map = {i: iid for iid, i in self.item_map.items()}
        
        self.n_users = len(self.user_ids)
        self.n_items = len(self.item_ids)
        
        # --- 2. GROUND TRUTH MATRICES (SPARSE) ---
        # We create two views of the same data for speed:
        # R_csr (Compressed Sparse Row): Fast for slicing a user's history (row).
        # R_csc (Compressed Sparse Column): Fast for finding who rated a specific movie (col).
        rows = [self.user_map[u] for u in ratings['UserID']]
        cols = [self.item_map[i] for i in ratings['MovieID']]
        data = ratings['binary_rating'].values
        
        # Note: We assume 'data' contains explicit 0s for dislikes if they exist in the dataframe.
        # csr_matrix stores 0s if they are explicitly passed in data/rows/cols.
        self.R_csr = csr_matrix((data, (rows, cols)), shape=(self.n_users, self.n_items))
        self.R_csc = csc_matrix((data, (rows, cols)), shape=(self.n_users, self.n_items))
        
        # --- 3. INITIALIZE BANDIT PARAMETERS ---
        # alpha[u, v] stores the number of times user u and v agreed (successes).
        # We initialize with the prior to avoid 0 values in Beta distribution.
        self.alpha = np.full((self.n_users, self.n_users), alpha_prior, dtype=np.float32)
        
        # n[u] stores the "weight of evidence" for user u (successes + failures + priors).
        # Initialized to (alpha_0 + beta_0) so that beta = n - alpha starts at beta_0.
        self.n = np.full(self.n_users, alpha_prior + beta_prior, dtype=np.float32)
        
        # --- 4. HISTORY TRACKING ---
        # Set of items recommended during the simulation for each user.
        # Used to ensure we don't recommend the same item twice to the same user.
        self.seen_mask = [set() for _ in range(self.n_users)]

    def simulate(self, n_simulations):
        """
        Runs the bandit simulation using the Replay method.
        
        Args:
            n_simulations (int): Number of recommendation steps to simulate.
            
        Returns:
            list: A list of [user_id, item_id, reward] for valid interactions.
        """
        list_of_recommendations = []
        
        print(f"Starting simulation for {n_simulations} iterations...")
        
        for t in range(n_simulations):
            # 1. Pick a random target user for this time step
            u_idx = np.random.randint(self.n_users)
            
            # ==========================================================
            # PHASE 1: RECOMMENDATION (Thompson Sampling)
            # ==========================================================
            
            # Calculate Beta parameters for all neighbors
            # Beta(v) = n(v) - alpha(u, v)
            # We clip to 0.001 to ensure strict positivity for numpy.random.beta
            beta_params = np.maximum(self.n - self.alpha[u_idx], 0.001)
            
            # Sample probabilities from Beta distribution (Vectorized)
            p = np.random.beta(self.alpha[u_idx], beta_params)
            
            # Exclude the user themselves from being their own neighbor
            p[u_idx] = -1.0 
            
            # Select Top K neighbors based on sampled scores
            # np.argpartition is O(N), much faster than sorting
            top_k_indices = np.argpartition(p, -self.k)[-self.k:]
            
            # Retrieve weights and ratings of these K neighbors
            neighbor_weights = p[top_k_indices]         # Shape: (k,)
            neighbor_ratings = self.R_csr[top_k_indices] # Shape: (k, n_items) - Sparse slicing
            
            # Compute Item Scores: Weighted sum of neighbor ratings
            # Matrix multiplication: (1, k) @ (k, items) -> (1, items)
            scores = neighbor_weights @ neighbor_ratings
            
            # Mask items already recommended during this simulation
            if self.seen_mask[u_idx]:
                # Setting score to -infinity ensures they are not picked
                scores[list(self.seen_mask[u_idx])] = -np.inf
                
            # Select the Best Item
            if scores.max() == -np.inf:
                # If all possible recommandations have been seen, skip this iteration
                continue
            if scores.max() <= 0:
                # If neighbors have no info or all scores are 0, explore randomly
                 rec_item_idx = np.random.randint(self.n_items)
            else:
                # Exploit: Pick item with highest score
                rec_item_idx = np.argmax(scores)
            
            # ==========================================================
            # PHASE 2: ORACLE & UPDATE (Replay Method)
            # ==========================================================
            
            # 1. Check for EXISTENCE in Ground Truth
            # In sparse matrices, we check if the index exists in the stored structure.
            # indptr tells us where the user's data starts and ends in the indices array.
            start_ptr = self.R_csr.indptr[u_idx]
            end_ptr = self.R_csr.indptr[u_idx + 1]
            user_history_indices = self.R_csr.indices[start_ptr:end_ptr]
            
            # Mark item as seen so it is not recommended again (even if we skip it)
            self.seen_mask[u_idx].add(rec_item_idx)
            
            if rec_item_idx not in user_history_indices:
                # CASE: MISSING DATA
                # The user never rated this movie in the dataset.
                # We cannot evaluate the recommendation. 
                # We simply skip to the next iteration.
                continue
                
            # 2. Retrieve the Rating Value
            # Since we know it exists, we can safely retrieve it.
            real_rating = self.R_csr[u_idx, rec_item_idx]
            
            # Retrieve real IDs for reporting
            real_user_id = self.rev_user_map[u_idx]
            real_item_id = self.rev_item_map[rec_item_idx]
            
            if real_rating > 0:
                # CASE: SUCCESS (Rating > 0, e.g., Liked)
                reward = 1
                list_of_recommendations.append([real_user_id, real_item_id, reward])
                
                # Update Parameters for Success:
                # 1. Update global count n for the target user
                self.n[u_idx] += 1
                
                # 2. Update alpha (agreement count) for ALL neighbors who also liked this item
                users_who_liked = self.R_csc[:, rec_item_idx].indices
                self.alpha[users_who_liked, u_idx] += 1
                self.alpha[u_idx, users_who_liked] += 1
                
            else:
                # CASE: FAILURE (Explicit 0 / Dislike)
                # The rating exists in DB but is 0 (bad movie).
                reward = 0
                list_of_recommendations.append([real_user_id, real_item_id, reward])
                
                # Update Parameters for Failure:
                # We update 'n' (total observations) but NOT 'alpha' (successes).
                # Since beta = n - alpha, this implicitly increases beta (failure count).
                self.n[u_idx] += 1

        print(f"Simulation finished. Processed {len(list_of_recommendations)} valid interactions.")
        return list_of_recommendations

In [6]:
# Initialize the bandit
knn_bandit = KNNBandit(k=10, ratings=ratings)

# Run simulation
print("Starting simulation...")
recommendations = knn_bandit.simulate(n_simulations=500000)
print(f"Simulation finished. Recommendation list: {recommendations}")
print(len(recommendations))

Starting simulation...
Starting simulation for 500000 iterations...
Simulation finished. Processed 204259 valid interactions.
Simulation finished. Recommendation list: [[np.int64(959), np.int64(2789), 1], [np.int64(2394), np.int64(2789), 1], [np.int64(1206), np.int64(2327), 1], [np.int64(2041), np.int64(2693), 1], [np.int64(1431), np.int64(847), 0], [np.int64(4715), np.int64(2789), 0], [np.int64(5893), np.int64(1178), 1], [np.int64(651), np.int64(2693), 1], [np.int64(3444), np.int64(1178), 1], [np.int64(3698), np.int64(589), 1], [np.int64(729), np.int64(2789), 1], [np.int64(2302), np.int64(2647), 1], [np.int64(1321), np.int64(2789), 1], [np.int64(1167), np.int64(1959), 1], [np.int64(4941), np.int64(1178), 1], [np.int64(2911), np.int64(1111), 1], [np.int64(5144), np.int64(2693), 1], [np.int64(4373), np.int64(2789), 1], [np.int64(5549), np.int64(1179), 1], [np.int64(3234), np.int64(1250), 1], [np.int64(3084), np.int64(257), 1], [np.int64(4430), np.int64(2789), 1], [np.int64(4497), np.int

In [7]:
print(recommendations[:10])

[[np.int64(959), np.int64(2789), 1], [np.int64(2394), np.int64(2789), 1], [np.int64(1206), np.int64(2327), 1], [np.int64(2041), np.int64(2693), 1], [np.int64(1431), np.int64(847), 0], [np.int64(4715), np.int64(2789), 0], [np.int64(5893), np.int64(1178), 1], [np.int64(651), np.int64(2693), 1], [np.int64(3444), np.int64(1178), 1], [np.int64(3698), np.int64(589), 1]]
